In [1]:
import os
import numpy as np
import pandas as pd
import geopandas as gpd
import rasterio as rio
import mercantile as merc
import matplotlib.pyplot as plt
import shapely
import folium

print(f'numpy={np.__version__}')
print(f'pandas={pd.__version__}')
print(f'geopandas={gpd.__version__}')
print(f'rasterio={rio.__version__}')
print(f'mercantile={merc.__version__}')
print(f'shapely={shapely.__version__}')
print(f'folium={folium.__version__}')

numpy=1.22.3
pandas=1.4.1
geopandas=0.10.2
rasterio=1.2.10
mercantile=1.2.1
shapely=1.8.0
folium=0.12.1.post1


In [3]:
'''
Import and inspect the chip locations
'''

# Import the coordinate features geojson as a geopandas dataframe
chip_features = gpd.read_file('./data/coordinates.geojson')

# Inspect the coordinate reference system (CRS) of the features
chip_features.crs

<Geographic 2D CRS: EPSG:4326>
Name: WGS 84
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: World.
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [4]:
'''
Get the centroid of the geometry using
For this operation to be accurate the geomtry needs to be transformed into a projected cooridnate system
'''

# Get the centroid of the geometry first in Web Mercartor
chip_features['centroid'] = chip_features.to_crs(epsg=3857).centroid

# Re-project the centroid back into WGS84
chip_features['centroid'] = chip_features['centroid'].to_crs(epsg=4326)

# Inspect
chip_features.head()

geometry  \
0  MULTIPOINT (-74.79529 40.94681, -74.79524 40.9...   

                     centroid  
0  POINT (-74.67207 40.98345)

In [5]:
'''
Only one MultiPoints feature has been provided in the dataset.
For ease of processing we will explode this single feature into its constituent parts.
'''

# Explode the multipoint geometry into the constiuent points
chip_locations = chip_features.explode(index_parts=False).reset_index(drop=True).loc[:, ('geometry')]

# Inspect the series
chip_locations.head()

0    POINT (-74.79529 40.94681)
1    POINT (-74.79524 40.94692)
2    POINT (-74.79468 40.94531)
3    POINT (-74.79457 40.94793)
4    POINT (-74.79430 40.94535)
Name: geometry, dtype: geometry

In [6]:
'''
Inspect the rasters.
To do this we will create a spatial dataframe that captures the metadata and extent of each raster in the data directory
'''

# Set the number of capture years
years = 37

# Set the directroy where the rasters are stored
raster_dir = './data/rasters/'

# Create a dictonary to store the data. We will use this to construct the dataframe
d = dict([(k, []) for k in ['file_name', 'tile', 'dtype', 'width', 'height', 'epsg', 'years', 'total_bands', 'bands_per_year', 'band_names', 'geometry']])

# Access all of the rasters in the directory
for raster in os.listdir(raster_dir):

    # Open each raster using rasterio
    with rio.open(os.path.join(raster_dir, raster), 'r') as src:
        
        # Get the count of bands as an integer
        count = int(src.meta['count'])

        # Get the raster tile
        tile_str = raster.rstrip('.tif')
        tile = (int(tile_str.split('_')[0]), int(tile_str.split('_')[1]), int(tile_str.split('_')[2]))

        # Use mercatile to get tile bounds
        bounds = merc.bounds(*tile)

        # Write the per raster metadata into the dictionary
        d['file_name'].append(raster)
        d['tile'].append(tile)
        d['dtype'].append(src.meta['dtype'])
        d['width'].append(src.meta['width'])
        d['height'].append(src.meta['height'])
        d['epsg'].append(src.meta['crs'].to_authority()[1])
        d['years'].append(years)
        d['total_bands'].append(count)
        d['bands_per_year'].append(int(count/years))
        d['band_names'].append([b[2:] for b in src.descriptions[:int(count/years)]])
        d['geometry'].append(shapely.geometry.box(bounds.west, bounds.south, bounds.east, bounds.north))

# Construct the spatial dataframe
raster_extents = gpd.GeoDataFrame(d)

# Set the crs to WGS84
raster_extents = raster_extents.set_crs(f'epsg:4326')

# Inspect the dataframe
raster_extents.head()

file_name            tile  dtype  width  height  epsg  years  \
0  299_383_10.tif  (299, 383, 10)  int32   1305     984  4326     37   
1  299_384_10.tif  (299, 384, 10)  int32   1305     988  4326     37   

   total_bands  bands_per_year  \
0          222               6   
1          222               6   

                                       band_names  \
0  [LS_B, LS_G, LS_R, LS_NIR, LS_SWIR1, LS_SWIR2]   
1  [LS_B, LS_G, LS_R, LS_NIR, LS_SWIR1, LS_SWIR2]   

                                            geometry  
0  POLYGON ((-74.53125 40.97990, -74.53125 41.244...  
1  POLYGON ((-74.53125 40.71396, -74.53125 40.979...

In [7]:
'''
Visualise the data
'''

# Image colorize function to make use of matplotlib colormaps
def colorize(array, cmap='viridis'):
    normalized = (array - array.min()) / (array.max() - array.min())    
    cm = plt.cm.get_cmap(cmap)    
    return cm(normalized)  

# Visualise the chip locations on an interactive map using the folium library
m = folium.Map(location = [chip_features['centroid'].y, chip_features['centroid'].x], tiles='CartoDB positron', zoom_start=10)

# Draw rasters
for _, r in raster_extents.iterrows():

    bounds = gpd.GeoSeries(r['geometry']).bounds
    bounds = bounds.iloc[0]

    with rio.open(os.path.join(raster_dir, r['file_name']), 'r') as src:

        # Rasterio stores the raster data as a numpy array so we can draw the image using ImageOverlay
        folium.raster_layers.ImageOverlay(
            image = colorize(src.read(220), cmap='viridis'), # We are going to visualise the Near Infrared band of the final year
            bounds = [[bounds['miny'], bounds['minx']], [bounds['maxy'], bounds['maxx']]],
            opacity=1,
            origin="upper",
            mercator_project=False
        ).add_to(m)

# Plot the raster extents
for _, r in raster_extents.iterrows():

    # First get the geometry as a geojson string
    bbx = gpd.GeoSeries(r['geometry']).to_json()
    
    # Define the folium geojson object and styling
    plot_geo = folium.GeoJson(
        data=bbx,
        style_function=lambda x: {
            'color': '#440154',
            'fillColor' : 'white'
        }
    )
    
    # Set the popup for the tiles
    folium.Popup(f"file_name: {r['file_name']}").add_to(plot_geo)

    # Ass to the map
    plot_geo.add_to(m)

# Plot the chip locations
for _, pt in chip_locations.iteritems():

    # Plot the chip locations as circles with a popup
    folium.Circle(
        location=[pt.y, pt.x],
        radius=10, 
        color='#ff3399', 
        fill=True, 
        popup=f"lat: {pt.y:.{4}f} lon: {pt.x:.{4}f}"
    ).add_to(m)

# Visualise map
m